In [51]:
# Ejecutar una vez 
import nltk
nltk.download('punkt')
nltk.download('stopwords')
nltk.download('wordnet')
nltk.download('omw-1.4')
nltk.download('word2vec_sample')

[nltk_data] Downloading package punkt to
[nltk_data]     C:\Users\Andres\AppData\Roaming\nltk_data...
[nltk_data]   Package punkt is already up-to-date!
[nltk_data] Downloading package stopwords to
[nltk_data]     C:\Users\Andres\AppData\Roaming\nltk_data...
[nltk_data]   Package stopwords is already up-to-date!
[nltk_data] Downloading package wordnet to
[nltk_data]     C:\Users\Andres\AppData\Roaming\nltk_data...
[nltk_data]   Package wordnet is already up-to-date!
[nltk_data] Downloading package omw-1.4 to
[nltk_data]     C:\Users\Andres\AppData\Roaming\nltk_data...
[nltk_data]   Package omw-1.4 is already up-to-date!
[nltk_data] Downloading package word2vec_sample to
[nltk_data]     C:\Users\Andres\AppData\Roaming\nltk_data...
[nltk_data]   Package word2vec_sample is already up-to-date!


True

In [52]:
import os
import re
import pandas as pd
import numpy as np
from numpy.random import randint, seed
import matplotlib.pyplot as plt
from PIL import Image

# NLP
import spacy

# Word embeddings
#!pip install gensim
import gensim

# WordCloud
from wordcloud import WordCloud

# Twitter y emojis
from twitter_text import extract_urls #Aqui es con text_parser para que funcione
import twitter_text as twt  # opcional si necesitas otras funciones del módulo
import emoji

# Scikit-learn
from sklearn.feature_extraction.text import CountVectorizer, TfidfVectorizer
from sklearn.metrics.pairwise import cosine_similarity,cosine_distances



# NLTK
import nltk
from nltk.tokenize import TweetTokenizer
from nltk.corpus import stopwords
from nltk.stem import WordNetLemmatizer
from nltk.data import find





from prettytable import PrettyTable



# Cálculo de la similitud entre textos (similitud del coseno)

In [53]:
# Importar tweets en inglés y filtrar por label1
df= pd.read_csv("../EnTrainTask12.csv",encoding='UTF8')
en_tr_lines_yes = df[df['label1'] == 'YES']['text'].dropna().tolist()
en_tr_lines_no = df[df['label1'] == 'NO']['text'].dropna().tolist()


# Importar tweets en español y filtrar por label1
df = pd.read_csv("../SpTrainTask12.csv", encoding='UTF-8')

sp_tr_lines_yes = df[df['label1'] == 'YES']['text'].dropna().tolist()
sp_tr_lines_no  = df[df['label1'] == 'NO']['text'].dropna().tolist()

In [54]:
# Transforma texto en lista de palabras limpias
def tk_er(t):
  t = re.sub('\W+', ' ', t.lower())
  tks = t.split()
  return (tks)


# Función de tokenizar de tweets
def mi_tokenizador(texto):

    '''
    urls = twt.extract_urls_with_indices(texto)
    for i in range(len(urls)-1,-1,-1):
        start, end = urls[i]['indices']
        texto = texto[:start] + texto[end:]
    '''
    urls = twt.extract_urls(texto, extract_urls_without_protocol = True)
    for url in urls:
        texto = texto.replace(url,'')
        #print(texto)
    
    # extraer emojis
    '''
    emos = twt.extract_emojis_with_indices(texto)
    for i in range(len(emos)-1,-1,-1):
        start, end = emos[i]['indices']
        texto = texto[:start] + texto[end:]
    '''
    texto = emoji.replace_emoji(texto, replace='') # elimina emojis
    
    # texto tokenizado --> lo ponemos en minúsculas, quitamos repeticiones y menciones
    tknzr = TweetTokenizer(preserve_case=False, reduce_len=True, strip_handles=True)
    tokens2 = tknzr.tokenize(texto)
    
    tokens2 = tk_er(' '.join(tokens2))

    return tokens2

In [55]:
# Función de limpiar tweets y eliminar stopwords
def mi_limpiador(texto):
    
    # Extraer URLs
    #print(f'mi texto: {texto}')
    urls = twt.extract_urls(texto, extract_urls_without_protocol = False)
    for url in urls:
        texto = texto.replace(url,'')

    
    # Extraer emojis
    texto = emoji.replace_emoji(texto, replace='')

    # Extraer hashtags
    hashtags = re.findall(r'#\w+', texto)
    for ht in hashtags:
        texto = texto.replace(ht, '')

    # Extraer menciones
    menciones = re.findall(r'@\w+', texto)
    for m in menciones:
        texto = texto.replace(m, '')
        

    texto = re.sub('\W+', ' ', texto.lower())

    # Extraer números (enteros o decimales)
    numeros = re.findall(r'\b\d+(?:\.\d+)?\b', texto)
    for n in numeros:
        texto = texto.replace(n, 'NUMBER')

    # Limpiar espacios sobrantes
    texto = re.sub(r'\s+', ' ', texto).strip()

    return texto

In [56]:
# Cargar stopwords
stop_en = set(stopwords.words("english"))
stop_sp = set(stopwords.words("spanish"))

# --- Cargar modelos de spaCy ---
nlp_en = spacy.load("en_core_web_sm")
nlp_sp = spacy.load("es_core_news_sm")


# --- INGLÉS ---
en_total_tweets_yes = []
for tweet in en_tr_lines_yes:
    serie_palabras=[t for t in mi_tokenizador((mi_limpiador(tweet))) if t.lower() not in stop_en]
    en_total_tweets_yes.append(' '.join(serie_palabras))


en_total_tweets_no = []
for tweet in en_tr_lines_no:
    serie_palabras=[t for t in mi_tokenizador((mi_limpiador(tweet))) if t.lower() not in stop_en]
    en_total_tweets_no.append(' '.join(serie_palabras))


# --- ESPAÑOL ---
sp_total_tweets_yes = []
for tweet in sp_tr_lines_yes:
    serie_palabras=[t for t in mi_tokenizador((mi_limpiador(tweet))) if t.lower() not in stop_sp]
    sp_total_tweets_yes.append(' '.join(serie_palabras))

sp_total_tweets_no = []
for tweet in sp_tr_lines_no:
    serie_palabras=[t for t in mi_tokenizador((mi_limpiador(tweet))) if t.lower() not in stop_sp]
    sp_total_tweets_no.append(' '.join(serie_palabras))




In [57]:

def pinta_matriz_dispersa(M, nombre_col=None, pre=2):
    filas, columnas = M.shape
    header = nombre_col != None
    pt = PrettyTable(nombre_col, header=header)
    for fila in range(3):
        vf = M.getrow(fila)
        _, cind = vf.nonzero()
        pt.add_row([round(vf[0, c],pre) if c in cind else '-' for c in range(columnas)])
 
    return pt 


In [58]:
# Funcion de similitud:

def similarity(Q,D):
  print("Q·D= ", round(Q.dot(D),2))
  print("|Q|= ", round(np.linalg.norm(Q),2))
  print("|D|= ", round(np.linalg.norm(D),2))
  similarity_score = Q.dot(D)/ (np.linalg.norm(Q) * np.linalg.norm(D))
  print("Similarity(D,Q)= ",round(similarity_score,2))
  print("=======\n")
  return

 ## Para Obtener el par de tweets más similar entre aquellos clasificados como 'Sexist' y el par más similar entre los clasificados como 'Non-Sexist'

 Se realizará por cada una de las representaciones realizadas en a, b, c, d, e, f, g

## a: "Bag of Words (binary)"

In [59]:
print('\nContadores binarios')
vec1 = CountVectorizer(binary=True)
vec2 = CountVectorizer(binary=True)
vec3 = CountVectorizer(binary=True)
vec4 = CountVectorizer(binary=True)

en_total_binary_yes = vec1.fit_transform(en_total_tweets_yes)
en_total_binary_no = vec2.fit_transform(en_total_tweets_no)
es_total_binary_yes = vec3.fit_transform(sp_total_tweets_yes)
es_total_binary_no = vec4.fit_transform(sp_total_tweets_no)

voca1 = list(vec1.get_feature_names_out())
voca2 = list(vec2.get_feature_names_out())
voca3 = list(vec3.get_feature_names_out())
voca4 = list(vec4.get_feature_names_out())



Contadores binarios


In [60]:
print(en_total_binary_yes.shape)
print(en_total_binary_no.shape)
print(es_total_binary_yes.shape)
print(es_total_binary_no.shape)

# Antes de eliminar stopwords
#(1137, 5343)
#(1733, 8302)
#(1560, 8402)
#(1634, 9486)

(1137, 5202)
(1733, 8169)
(1560, 8193)
(1634, 9280)


In [61]:
print('Ingles Sex')
print(pinta_matriz_dispersa(en_total_binary_yes, voca1, 4))
print('Ingles No-Sex')
print(pinta_matriz_dispersa(en_total_binary_no, voca2, 4))
print('Español Sex')
print(pinta_matriz_dispersa(es_total_binary_yes, voca3, 4))
print('Español No-Sex')
print(pinta_matriz_dispersa(es_total_binary_no, voca4, 4))

Ingles Sex
+----+-----+-------+-------+----+-----+------------+-----+-------+------+------+--------+-----+----+------+---------+-------+------+-----+------+-------+----+---------+-----+-------+-----+---------+-----+-----+-----+------+-----+---------+----+--------+-----+-----+--------+----------+---------+------+---------+----------+----------+-----------+----------+------------+----------+----------+-----+-------+--------+--------+---------+---------+----------+-----------+--------+-----------+--------+--------------+-------------+-----------+---------+----------------+-------------+----------+------------+-------------+--------+---------+-----------+----------+-------------+------------+------------+---------+--------+-----+--------+--------+-----------+---------+----------+-----------+----------+-------+---------+------+--------+----------+-----+-------+----------+----------+---------+-----------+------------+---------+-------+---------+----------+-------+----------+------------+----

## b: "Bag of Words (Term-Frequency) without normalization"

In [62]:
print('\nTF sin normalizar')

vec1 = TfidfVectorizer(norm=None, use_idf=False)
vec2 = TfidfVectorizer(norm=None, use_idf=False)
vec3 = TfidfVectorizer(norm=None, use_idf=False)
vec4 = TfidfVectorizer(norm=None, use_idf=False)

en_total_TF_yes = vec1.fit_transform(en_total_tweets_yes)
en_total_TF_no = vec2.fit_transform(en_total_tweets_no)
es_total_TF_yes = vec3.fit_transform(sp_total_tweets_yes)
es_total_TF_no = vec4.fit_transform(sp_total_tweets_no)

voca1 = list(vec1.get_feature_names_out())
voca2 = list(vec2.get_feature_names_out())
voca3 = list(vec3.get_feature_names_out())
voca4 = list(vec4.get_feature_names_out())



TF sin normalizar


In [63]:
print('Ingles Sex')
print(pinta_matriz_dispersa(en_total_TF_yes, voca1, 4))
print('Ingles No-Sex')
print(pinta_matriz_dispersa(en_total_TF_no, voca2, 4))
print('Español Sex')
print(pinta_matriz_dispersa(es_total_TF_yes, voca3, 4))
print('Español No-Sex')
print(pinta_matriz_dispersa(es_total_TF_no, voca4, 4))

Ingles Sex
+----+-----+-------+-------+----+-----+------------+-----+-------+------+------+--------+-----+----+------+---------+-------+------+-----+------+-------+----+---------+-----+-------+-----+---------+-----+-----+-----+------+-----+---------+----+--------+-----+-----+--------+----------+---------+------+---------+----------+----------+-----------+----------+------------+----------+----------+-----+-------+--------+--------+---------+---------+----------+-----------+--------+-----------+--------+--------------+-------------+-----------+---------+----------------+-------------+----------+------------+-------------+--------+---------+-----------+----------+-------------+------------+------------+---------+--------+-----+--------+--------+-----------+---------+----------+-----------+----------+-------+---------+------+--------+----------+-----+-------+----------+----------+---------+-----------+------------+---------+-------+---------+----------+-------+----------+------------+----

## c: "TF-IDF based on words with 'l1' normalization"

In [64]:
#SIN SUAVIZADO
print("\nTF-IDF: sin suavizado y normalización 'l1'")
#CON SUAVIZADO
#print("\nTF-IDF: con idf suavizado y normalización 'l1'")
#vec = TfidfVectorizer(norm='l1', smooth_idf=True)

vec1 = TfidfVectorizer(norm='l1', smooth_idf=False)
vec2 = TfidfVectorizer(norm='l1', smooth_idf=False)
vec3 = TfidfVectorizer(norm='l1', smooth_idf=False)
vec4 = TfidfVectorizer(norm='l1', smooth_idf=False)

en_total_TFIDF_yes = vec1.fit_transform(en_total_tweets_yes)
en_total_TFIDF_no = vec2.fit_transform(en_total_tweets_no)
es_total_TFIDF_yes = vec3.fit_transform(sp_total_tweets_yes)
es_total_TFIDF_no = vec4.fit_transform(sp_total_tweets_no)

voca1 = list(vec1.get_feature_names_out())
voca2 = list(vec2.get_feature_names_out())
voca3 = list(vec3.get_feature_names_out())
voca4 = list(vec4.get_feature_names_out())


TF-IDF: sin suavizado y normalización 'l1'


In [65]:
print('Ingles Sex')
print(pinta_matriz_dispersa(en_total_TFIDF_yes, voca1, 4))
print('Ingles No-Sex')
print(pinta_matriz_dispersa(en_total_TFIDF_no, voca2, 4))
print('Español Sex')
print(pinta_matriz_dispersa(es_total_TFIDF_yes, voca3, 4))
print('Español No-Sex')
print(pinta_matriz_dispersa(es_total_TFIDF_no, voca4, 4))

Ingles Sex
+----+-----+-------+-------+----+-----+------------+-----+-------+------+------+--------+-----+----+------+---------+-------+------+-----+------+-------+----+---------+-----+-------+-----+---------+-----+-----+-----+------+-----+---------+----+--------+-----+-----+--------+----------+---------+------+---------+----------+----------+-----------+----------+------------+----------+----------+-----+-------+--------+--------+---------+---------+----------+-----------+--------+-----------+--------+--------------+-------------+-----------+---------+----------------+-------------+----------+------------+-------------+--------+---------+-----------+----------+-------------+------------+------------+---------+--------+-----+--------+--------+-----------+---------+----------+-----------+----------+-------+---------+------+--------+----------+-----+-------+----------+----------+---------+-----------+------------+---------+-------+---------+----------+-------+----------+------------+----

## d: "TF-IDF based on words with 'l2' normalization"

In [66]:
print("\nTF-IDF: con idf suavizado y normalización 'l2'")

vec1 = TfidfVectorizer(norm='l2', smooth_idf=True)
vec2 = TfidfVectorizer(norm='l2', smooth_idf=True)
vec3 = TfidfVectorizer(norm='l2', smooth_idf=True)
vec4 = TfidfVectorizer(norm='l2', smooth_idf=True)

en_total_TFIDFL2_yes = vec1.fit_transform(en_total_tweets_yes)
en_total_TFIDFL2_no = vec2.fit_transform(en_total_tweets_no)
es_total_TFIDFL2_yes = vec3.fit_transform(sp_total_tweets_yes)
es_total_TFIDFL2_no = vec4.fit_transform(sp_total_tweets_no)

voca1 = list(vec1.get_feature_names_out())
voca2 = list(vec2.get_feature_names_out())
voca3 = list(vec3.get_feature_names_out())
voca4 = list(vec4.get_feature_names_out())


TF-IDF: con idf suavizado y normalización 'l2'


In [67]:
print('Ingles Sex')
print(pinta_matriz_dispersa(en_total_TFIDFL2_yes, voca1, 4))
print('Ingles No-Sex')
print(pinta_matriz_dispersa(en_total_TFIDFL2_no, voca2, 4))
print('Español Sex')
print(pinta_matriz_dispersa(es_total_TFIDFL2_yes, voca3, 4))
print('Español No-Sex')
print(pinta_matriz_dispersa(es_total_TFIDFL2_no, voca4, 4))

Ingles Sex
+----+-----+-------+-------+----+-----+------------+-----+-------+------+------+--------+-----+----+------+---------+-------+------+-----+------+-------+----+---------+-----+-------+-----+---------+-----+-----+-----+------+-----+---------+----+--------+-----+-----+--------+----------+---------+------+---------+----------+----------+-----------+----------+------------+----------+----------+-----+-------+--------+--------+---------+---------+----------+-----------+--------+-----------+--------+--------------+-------------+-----------+---------+----------------+-------------+----------+------------+-------------+--------+---------+-----------+----------+-------------+------------+------------+---------+--------+-----+--------+--------+-----------+---------+----------+-----------+----------+-------+---------+------+--------+----------+-----+-------+----------+----------+---------+-----------+------------+---------+-------+---------+----------+-------+----------+------------+----

In [ ]:
# Output the features.
# print(vec.get_feature_names_out())# Output the features.
# print(vec.get_feature_names_out())

# # The cosine similarity matrix.
# 1 - np.round(pairwise_distances(X, metric="cosine"),3)
# np.round(cosine_similarity(X),3)

# Q1 = ['machine intelligence']
# Y=vec.transform(Q1)
# print(pinta_matriz_dispersa(Y, voca, 4))
# cosine_similarity(Y,X)

# Q2 = ['machine learning']
# Y=vec.transform(Q2)
# print(pinta_matriz_dispersa(Y, voca, 4))
# cosine_similarity(Y,X)

NameError: name 'vec' is not defined

## e: "Bigrams of Words (Term-Frequency) without normalization"

In [69]:
vectorizer = TfidfVectorizer(ngram_range=(2,2), analyzer='word', use_idf=False, norm=None)

TF_bigrams_en_yes = vectorizer.fit_transform(en_total_tweets_yes).toarray()
bigrams1 = vectorizer.get_feature_names_out()
print('La matriz de bigramas para Ingles Sex')
print(bigrams1)         # Lista de bigramas
print(TF_bigrams_en_yes)      # Matriz TF

print('\n ----------------------------------------- \n')
TF_bigrams_en_no = vectorizer.fit_transform(en_total_tweets_no).toarray()
bigrams2 = vectorizer.get_feature_names_out()
print('La matriz de bigramas para Ingles No-Sex')
print(bigrams2)         # Lista de bigramas
print(TF_bigrams_en_no)      # Matriz TF

print('\n ----------------------------------------- \n')
TF_bigrams_es_yes = vectorizer.fit_transform(sp_total_tweets_yes).toarray()
bigrams3 = vectorizer.get_feature_names_out()
print('La matriz de bigramas para Español Sex')
print(bigrams3)         # Lista de bigramas
print(TF_bigrams_es_yes)      # Matriz TF

print('\n ----------------------------------------- \n')
TF_bigrams_es_no = vectorizer.fit_transform(sp_total_tweets_no).toarray()
bigrams4 = vectorizer.get_feature_names_out()
print('La matriz de bigramas para Español No-Sex')
print(bigrams4)         # Lista de bigramas
print(TF_bigrams_es_no)      # Matriz TF



La matriz de bigramas para Ingles Sex
['0r watching' '0th power' '1960s part' ... 'zone concede' 'ˡᵒᵒᵏ ˡⁱᵏᵉ'
 'ˡⁱᵏᵉ ᵇⁱᵗᶜʰ']
[[0. 0. 0. ... 0. 0. 0.]
 [0. 0. 0. ... 0. 0. 0.]
 [0. 0. 0. ... 0. 0. 0.]
 ...
 [0. 0. 0. ... 0. 0. 0.]
 [0. 0. 0. ... 0. 0. 0.]
 [0. 0. 0. ... 0. 0. 0.]]

 ----------------------------------------- 

La matriz de bigramas para Ingles No-Sex
['000s break' '009 made' '06jan reusable' ... '𝙩𝙖𝙠𝙚 𝙘𝙖𝙧𝙚' '𝙩𝙤 𝙩𝙖𝙠𝙚'
 '𝙮𝙤𝙪 lambert']
[[0. 0. 0. ... 0. 0. 0.]
 [0. 0. 0. ... 0. 0. 0.]
 [0. 0. 0. ... 0. 0. 0.]
 ...
 [0. 0. 0. ... 0. 0. 0.]
 [0. 0. 0. ... 0. 0. 0.]
 [0. 0. 0. ... 0. 0. 0.]]

 ----------------------------------------- 

La matriz de bigramas para Español Sex
['0number1 hilo' '1010en línea' '1er tuit' ... 'útil convertían'
 '𝐄𝐦𝐩𝐨𝐝𝐞𝐫𝐚𝐝𝐚𝐬 dirigido' '𝐏𝐫𝐨𝐲𝐞𝐜𝐭𝐨 𝐄𝐦𝐩𝐨𝐝𝐞𝐫𝐚𝐝𝐚𝐬']
[[0. 0. 0. ... 0. 0. 0.]
 [0. 0. 0. ... 0. 0. 0.]
 [0. 0. 0. ... 0. 0. 0.]
 ...
 [0. 0. 0. ... 0. 0. 0.]
 [0. 0. 0. ... 0. 0. 0.]
 [0. 0. 0. ... 0. 0. 0.]]

 -------------------------------------

## f: "Trigram of Characters (Term-Frequency) without normalization"

In [70]:
vectorizer = TfidfVectorizer(ngram_range=(3,3), analyzer='word', use_idf=False, norm=None)

TF_trigramas_en_yes = vectorizer.fit_transform(en_total_tweets_yes).toarray()
tigramas1 = vectorizer.get_feature_names_out()
print('La matriz de trigramas para Ingles Sex')
print(tigramas1)         # Lista de bigramas
print(TF_trigramas_en_yes)      # Matriz TF

print('\n ----------------------------------------- \n')
TF_trigramas_en_no = vectorizer.fit_transform(en_total_tweets_no).toarray()
tigramas2 = vectorizer.get_feature_names_out()
print('La matriz de trigramas para Ingles No-Sex')
print(tigramas2)         # Lista de bigramas
print(TF_trigramas_en_no)      # Matriz TF

print('\n ----------------------------------------- \n')
TF_trigramas_es_yes = vectorizer.fit_transform(sp_total_tweets_yes).toarray()
tigramas3 = vectorizer.get_feature_names_out()
print('La matriz de trigramas para Español Sex')
print(tigramas3)         # Lista de bigramas
print(TF_trigramas_es_yes)      # Matriz TF

print('\n ----------------------------------------- \n')
TF_trigramas_es_no = vectorizer.fit_transform(sp_total_tweets_no).toarray()
tigramas4 = vectorizer.get_feature_names_out()
print('La matriz de trigramas para Español No-Sex')
print(tigramas4)         # Lista de bigramas
print(TF_trigramas_es_no)      # Matriz TF


La matriz de trigramas para Ingles Sex
['0r watching sodomize' '0th power men' '1960s part feminist' ...
 'zher partner hidden' 'zone concede abortion' 'ˡᵒᵒᵏ ˡⁱᵏᵉ ᵇⁱᵗᶜʰ']
[[0. 0. 0. ... 0. 0. 0.]
 [0. 0. 0. ... 0. 0. 0.]
 [0. 0. 0. ... 0. 0. 0.]
 ...
 [0. 0. 0. ... 0. 0. 0.]
 [0. 0. 0. ... 0. 0. 0.]
 [0. 0. 0. ... 0. 0. 0.]]

 ----------------------------------------- 

La matriz de trigramas para Ingles No-Sex
['000s break oppression' '009 made rape' '06jan reusable cloth' ...
 '𝙩𝙖𝙠𝙚 𝙘𝙖𝙧𝙚 𝙤𝙛' '𝙩𝙤 𝙩𝙖𝙠𝙚 𝙘𝙖𝙧𝙚' '𝙮𝙤𝙪 lambert 𝙣𝙚𝙚𝙙']
[[0. 0. 0. ... 0. 0. 0.]
 [0. 0. 0. ... 0. 0. 0.]
 [0. 0. 0. ... 0. 0. 0.]
 ...
 [0. 0. 0. ... 0. 0. 0.]
 [0. 0. 0. ... 0. 0. 0.]
 [0. 0. 0. ... 0. 0. 0.]]

 ----------------------------------------- 

La matriz de trigramas para Español Sex
['1010en línea enhttps' '1er tuit pretexto' '1na putofobia chupa' ...
 'útil convertían relaciónes' '𝐄𝐦𝐩𝐨𝐝𝐞𝐫𝐚𝐝𝐚𝐬 dirigido prevenir'
 '𝐏𝐫𝐨𝐲𝐞𝐜𝐭𝐨 𝐄𝐦𝐩𝐨𝐝𝐞𝐫𝐚𝐝𝐚𝐬 dirigido']
[[0. 0. 0. ... 0. 0. 0.]
 [0. 0. 0. ... 0. 0. 0.]
 [0. 0. 

## g: embeddings word2vec (promedio)

Se carga el modelo en Ingles y Español

In [71]:
# Cargar el modelo de embeding pre-entrenados del NLTK
word2vec_sample = str(find('models/word2vec_sample/pruned.word2vec.txt'))
model = gensim.models.KeyedVectors.load_word2vec_format(word2vec_sample, binary=False)
# Número palabras
print("#palabras: ", len(model.key_to_index))
# Tamaño del vector
print ("#componentes: ",len(model['class']))

#palabras:  43981
#componentes:  300


In [72]:
# el modelo de nltk solo es para el inglés, esta instrucción fallará:

print(model.similarity("king", "queen"))
#Buscar n palabras similares a una dada

print(model.most_similar(positive=['football'], topn = 10))
#Palabras que no son de un dominio temático

print(model.doesnt_match(['breakfast','house', 'dinner', 'lunch']))

0.65109587
[('soccer', 0.7313547134399414), ('Football', 0.7124834656715393), ('basketball', 0.6682467460632324), ('athletics', 0.6265193223953247), ('baseball', 0.6162000298500061), ('sports', 0.5927177667617798), ('coaches', 0.5791538953781128), ('athletic', 0.5767539739608765), ('Soccer', 0.5632802248001099), ('hockey', 0.5496212840080261)]
house


In [73]:

ruta = "SBW-vectors-300-min5.bin.gz"
model_es = gensim.models.KeyedVectors.load_word2vec_format(ruta, binary=True)

print("#palabras:", len(model_es.key_to_index))
print("#componentes:", model_es.vector_size)


#palabras: 1000653
#componentes: 300


In [74]:
# Probamos que los modelos están funcionales

print(model_es.similarity("rey", "reina"))
#Buscar n palabras similares a una dada

print(model_es.most_similar(positive=['futbol'], topn = 10))
#Palabras que no son de un dominio temático

print(model_es.doesnt_match(['desayuno','casa', 'cena', 'comida']))

0.7253803
[('balompié', 0.8196004629135132), ('fútbol', 0.7768495678901672), ('soccer', 0.732681393623352), ('beisbol', 0.7146016955375671), ('basquetbol', 0.7087005972862244), ('básquetbol', 0.705640435218811), ('futsal', 0.6871283054351807), ('Futbol', 0.6865250468254089), ('basquet', 0.6808387041091919), ('futbolístico', 0.6743321418762207)]
casa


Con los modelos en español e ingles se comparan con los tweets sacando primero los tokens, se vectoriza por tweet y se saca el promedio.

In [75]:
# Función para calcular embedding promedio de un tweet tokenizado
def tweet_embedding_average(tweet_tokens, model):
    vectors = [model[token] for token in tweet_tokens if token in model.key_to_index]
    if vectors:
        return np.mean(vectors, axis=0)
    else:
        return np.zeros(model.vector_size)

# Función para procesar listas de tweets en batch
def batch_tweets_embedding(tweets_list, model, tokenizer):
    # Tokenizar todos los tweets en batch
    tokenized_tweets = [tokenizer(tweet) for tweet in tweets_list]
    # Calcular embeddings promedio de cada tweet
    embeddings = np.array([tweet_embedding_average(tokens, model) for tokens in tokenized_tweets])
    return embeddings

# Aplicar a tus listas y modelos
en_avg_yes = batch_tweets_embedding(en_total_tweets_yes, model, tk_er)
en_avg_no  = batch_tweets_embedding(en_total_tweets_no, model, tk_er)
es_avg_yes = batch_tweets_embedding(sp_total_tweets_yes, model_es, tk_er)
es_avg_no  = batch_tweets_embedding(sp_total_tweets_no, model_es, tk_er)

print("Shape ejemplo:", en_avg_yes.shape)  # (num_tweets, tamaño_vector)

# los embeddings promedio de cada tweet
print("Shape Ingles Sex:", en_avg_yes.shape)  # (num_tweets, 300)
print("Shape Ingles No-Sex:", en_avg_no.shape)  # (num_tweets, 300)

print("Shape Español Sex:", es_avg_yes.shape)  # (num_tweets, 300)
print("Shape Español No-Sex:", es_avg_no.shape)  # (num_tweets, 300)


Shape ejemplo: (1137, 300)
Shape Ingles Sex: (1137, 300)
Shape Ingles No-Sex: (1733, 300)
Shape Español Sex: (1560, 300)
Shape Español No-Sex: (1634, 300)


In [76]:
print(en_avg_yes)

[[ 0.01807713  0.00757657 -0.01125029 ... -0.02334916  0.01481577
   0.00346017]
 [ 0.02504961  0.01002807  0.02217661 ... -0.01430091 -0.01813371
  -0.0020317 ]
 [ 0.02923016  0.02806506 -0.02450341 ... -0.01189107  0.02148125
  -0.02302519]
 ...
 [ 0.0084272   0.00778594  0.00358832 ... -0.01720453 -0.02763842
  -0.00249884]
 [ 0.0084055   0.028619    0.0067684  ... -0.0026907  -0.06376066
   0.0303998 ]
 [ 0.00553734  0.0034319   0.01347421 ...  0.00405423 -0.02943501
   0.0201237 ]]


## Se realiza la relacion del coseno para cada matriz

Se crea la funcion el diccionario de los resultados anteriores y se imprimen los resultados

In [ ]:

# Función para obtener los dos elementos más similares dentro de una matriz
def top_2_similares(matrix):
    sim = cosine_similarity(matrix)
    np.fill_diagonal(sim, -1)  # ignorar similitud consigo mismo
    idx_flat = np.argpartition(sim.flatten(), -2)[-2:]
    idx_row_col = [np.unravel_index(i, sim.shape) for i in idx_flat]
    valores = [sim[i,j] for i,j in idx_row_col]
    return idx_row_col, valores

# Diccionario con todas las matrices y los tweets originales
matrices = {
    'a: Bag of Words (binary)': [
        (en_total_binary_yes, en_total_tweets_yes),
        (en_total_binary_no, en_total_tweets_no),
        (es_total_binary_yes, sp_total_tweets_yes),
        (es_total_binary_no, sp_total_tweets_no)
    ],
    'b: Bag of Words (TF)': [
        (en_total_TF_yes, en_total_tweets_yes),
        (en_total_TF_no, en_total_tweets_no),
        (es_total_TF_yes, sp_total_tweets_yes),
        (es_total_TF_no, sp_total_tweets_no)
    ],
    'c: TF-IDF l1': [
        (en_total_TFIDF_yes, en_total_tweets_yes),
        (en_total_TFIDF_no, en_total_tweets_no),
        (es_total_TFIDF_yes, sp_total_tweets_yes),
        (es_total_TFIDF_no, sp_total_tweets_no)
    ],
    'd: TF-IDF l2': [
        (en_total_TFIDFL2_yes, en_total_tweets_yes),
        (en_total_TFIDFL2_no, en_total_tweets_no),
        (es_total_TFIDFL2_yes, sp_total_tweets_yes),
        (es_total_TFIDFL2_no, sp_total_tweets_no)
    ],
    'e: TF Bigrams': [
        (TF_bigrams_en_yes, en_total_tweets_yes),
        (TF_bigrams_en_no, en_total_tweets_no),
        (TF_bigrams_es_yes, sp_total_tweets_yes),
        (TF_bigrams_es_no, sp_total_tweets_no)
    ],
    'f: TF Trigrams': [
        (TF_trigramas_en_yes, en_total_tweets_yes),
        (TF_trigramas_en_no, en_total_tweets_no),
        (TF_trigramas_es_yes, sp_total_tweets_yes),
        (TF_trigramas_es_no, sp_total_tweets_no)
    ],
    'g: Word2Vec promedio': [
        (en_avg_yes, en_total_tweets_yes),
        (en_avg_no, en_total_tweets_no),
        (es_avg_yes, sp_total_tweets_yes),
        (es_avg_no, sp_total_tweets_no)
    ]
}

categorias = ['ingles sex', 'ingles no-sex', 'español sex', 'español no-sex']

# Recorrer todas las matrices y categorías
for nombre, mats in matrices.items():
    print(f"\n--- {nombre} ---")
    for cat, (mat, tweets) in zip(categorias, mats):
        idx, vals = top_2_similares(mat)
        print(f"\n{cat}:")
        for (i,j), v in zip(idx, vals):
            print(f"  Tweets {i} y {j}, similitud: {v:.4f}")
            print(f"    Tweet {i}: {tweets[i]}")
            print(f"    Tweet {j}: {tweets[j]}")



--- a: Bag of Words (binary) ---

ingles sex:
  Tweets 825 y 832, similitud: 1.0000
    Tweet 825: masculine urge spank women half size
    Tweet 832: masculine urge spank women half size
  Tweets 832 y 825, similitud: 1.0000
    Tweet 832: masculine urge spank women half size
    Tweet 825: masculine urge spank women half size

ingles no-sex:
  Tweets 1586 y 164, similitud: 1.0000
    Tweet 1586: account temporarily unavailable violates twitter media policy learn
    Tweet 164: account temporarily unavailable violates twitter media policy learn
  Tweets 164 y 1586, similitud: 1.0000
    Tweet 164: account temporarily unavailable violates twitter media policy learn
    Tweet 1586: account temporarily unavailable violates twitter media policy learn

español sex:
  Tweets 475 y 476, similitud: 1.0000
    Tweet 475: frente alta lengua larga falda corta
    Tweet 476: frente alta lengua larga falda corta
  Tweets 476 y 475, similitud: 1.0000
    Tweet 476: frente alta lengua larga falda c

En lo de ingles no se ve mucha diferencia pero en los de español si se ve que dependiendo de el método utilizado los resultados varian en cuanto a los valores con mayor similitud.